# Run various tests on models

In [1]:
from game.game import Game
from game.data.generator import create_numbers
import torch
import os

In [2]:
# loads checkpoint and does one epoch, shows acc on validation set
def load(last_save, model_size, model_number, run_number, vocab, sender, receiver, embedding, length=1):
    epochs = last_save + 1
    save_name = "game/models/game{}_{}_{}_{}_{}_{}_{}".format(model_size, model_number, run_number, vocab, sender, receiver, embedding)
    if(length > 1):
        save_name = "{}_{}".format(save_name, length)
    

    params = [
        '--batch_size=1',
        '--n_epochs={}'.format(epochs),
        '--vocab_size={}'.format(vocab),
        '--sender_hidden={}'.format(sender),
        '--receiver_hidden={}'.format(receiver),
        '--lr=0.001',
        '--max_len={}'.format(length),
        '--sender_entropy=0.5',
        '--sender_embedding={}'.format(embedding),
        '--receiver_embedding={}'.format(embedding),
        '--validation_freq=10',
        '--train_data=game/data/train10.txt',
        '--validation_data=game/data/validation10.txt',
        '--load_from_checkpoint={}_{}.tar'.format(save_name, last_save)
    ]
    game = Game(params)
    game.play()
    return game

In [100]:
def predict_and_print(model, inputs, labels):
    inputs_tensor = torch.FloatTensor(inputs)
    labels_tensor = torch.FloatTensor(labels)
    prediction = model.game.forward(inputs_tensor,labels_tensor)
    messages = prediction[1].message.tolist()
    outputs = prediction[1].receiver_output.tolist()
    for q in range(len(outputs)):
        print("{} {} {} {}".format(inputs[q], messages[q], outputs[q], labels[q]))
    unique_outputs = set([item[0] for item in outputs])
    number_unique = len(unique_outputs)
    message_strings = ["_".join([ str(m) for m in message]) for message in messages]
    acc = prediction[1].aux['acc'].mean().item()            
    print("Unique outputs: {}: {}".format(number_unique, unique_outputs))
    print("Accuracy: {}".format(acc))
    return acc, number_unique, message_strings


In [79]:
def calc_polysemy(inputs, labels, message_strings):
    message_inputs = {}
    for r in range(len(inputs)):
        input = ",".join([ str(i) for i in inputs[r]])
        message = message_strings[r]
        label = labels[r][0]
        label_dict = message_inputs.get(message, {})
        message_inputs[message] = label_dict
        input_list = label_dict.get(label, [])
        input_list.append(input)
        message_inputs[message][label] = input_list

    polysemous = 0
    polysemous_ = 0
    polysemous_input = 0
    for message, labels in message_inputs.items():
        if (len(labels)> 2):
            polysemous_ += 1
            polysemous_input += 1
        elif (len(labels)> 1):
            polysemous += 1
            polysemous_input += 1
        else:
            for label, inputs in labels.items(): 
                if (len(inputs)> 1):
                    polysemous_input += 1
    print("Polysemous messages, 2 or more inputs: {}, {}".format(polysemous_input, polysemous_input/len(message_inputs)))
    print("Polysemous messages, 2 or more labels: {}, {}".format(polysemous, polysemous/len(message_inputs)))
    print("Polysemous messages, 3 or more labels: {}, {}".format(polysemous_, polysemous_/len(message_inputs)))

In [4]:
extra_tests = {}
def test_above_limit(game, start, end, number_of_samples):
    # creates more samples for model to predict
    inputs, labels = extra_tests.get((start, end, number_of_samples), (None, None))
    if(inputs is None or labels is None):
        inputs, labels = create_numbers(end, number_of_samples, False, False, start)
        extra_tests[(start, end, number_of_samples)] = (inputs, labels)
        print("Inputs: {}".format(inputs))
        print("Labels: {}".format(labels))
        
    print("Testing {} samples of numbers that sum up to [{} - {}]".format(number_of_samples, start, end))
    return predict_and_print(game, inputs, labels)

In [98]:
def test_all_set(game, n):
    inputs = []
    labels = []
    for i in range(n+1):
        for j in range(n+1):
            if i+j <= n:
                inputs.append([i, j])
                labels.append([i+j]) 
    print("Testing {} samples of numbers that sum up to {}".format(len(inputs), n))
    a, m, message_strings = predict_and_print(game, inputs, labels)
    calc_polysemy(inputs, labels, message_strings)
    return a, m, message_strings

In [6]:
def test_validation_only(game):
    frame = game.trainer.validation_data.dataset.frame
    inputs = [f[0].tolist() for f in frame]
    labels = [f[1].tolist() for f in frame]
    return predict_and_print(game, inputs, labels)

In [7]:
def test_some_other_numbers(game):
    inputs = [[9.0, 0.2], [0., 0.3],[6.0, 4.0],[6.0, 4.0],[9.0, 1.0],[9.0, 1.0],[9.0, 1.0],[1.0, 1.0],[1.0, 1.0],[1.0, 1.0], [0.0, 1.0], [0.0, 0.0], [-1.0, 4.0], [5.0, -2.0], [-1.0, 0.0], [-2.0, -2.0], [-9.0, -1.0], [8.0, -3.0], [-10.0, -10.0]]
    labels = [[9.2],[.3],[10.],[10.],[10.],[10.],[10.],[2.0],[2.0],[2.0],[1.0],[0.0],[3.0],[3.0], [-1.0], [-4.0], [-10.0], [5.0], [-20.0]]
    return predict_and_print(game, inputs, labels)

In [101]:
def test_synonymy(game, n, repeat):
    limit = n+1
    accs_input = {}
    messages_input = {}
    accs_label = {}
    messages_label = {}
    for i in range(limit):
        for j in range(limit):
            if(i+j <= n):
                inputs = []
                labels = []
                for p in range(repeat):
                    inputs.append([i, j])
                    labels.append([i+j]) 
                
                a, m, o = predict_and_print(game, inputs, labels)
                
                input = (inputs[0][0],inputs[0][1])
                label = labels[0][0]
                accs_input[input] = a
                messages_input[input] = m
                
                l = messages_label.get(label, [])
                l.append(o)
                messages_label[label] = l
                
                l = accs_label.get(label, [])
                l.append(a)
                accs_label[label] = l
                
    for i in range(limit):
        messages = [message for message_set in messages_label[i] for message in message_set]
        messages_label[i] = len(set(messages))
        accs_label[i] = sum(accs_label[i])/len(accs_label[i])
        
    print("Unique messages per labels: {}".format(messages_label))    
    print("Unique messages per input: {}".format(messages_input))
    print("Accuracies per input: {}".format(accs_input))
    return accs_label, messages_label, _

In [9]:
def test_various_ranges(game, start_numbers, end_numbers, n_samples):
    accs = []
    ns_symbols = []
    for i in range(len(start_numbers)):  
        acc, n_symbols, _ = test_above_limit(game, start_numbers[i], end_numbers[i], n_samples[i])
        accs.append(acc)
        ns_symbols.append(n_symbols)
    print("Accuracies: {}".format(accs))
    print("Number of messages: {}".format(ns_symbols))
    return accs, ns_symbols, _

In [10]:
def run_test(games, test):
    accs = []
    ns_symbols= []
    
    for i in range(len(games)):
        print("\n--------")
        print("Running test for game {}".format(i))
        acc, n_symbols, _ = test(games[i])
        accs.append(acc)
        ns_symbols.append(n_symbols)
        
    print("\n--------")
    print("All games:")
    for i in range(len(accs)):
        print("Game {},  Number of messages: {}, Accuracy: {}".format(i, ns_symbols[i], accs[i]))

In [45]:
games10 = [
    load(6000, 10, 14, 1, 16, 16, 16, 5),#game10_14_1_16_16_16_5_6000.tar
    load(1500, 10, 14, 1, 32, 32, 32, 7), #game10_14_1_32_32_32_7_1500.tar
    load(1500, 10, 14, 1, 32, 64, 32, 7), # game10_14_1_32_64_32_7_1500.tar
    load(1500, 10, 14, 1, 64, 64, 64, 7), #game10_14_1_64_64_64_7_1500.tar
    load(1500, 10, 14, 1, 64, 128, 64, 8), # game10_14_1_64_128_64_8_1500.tar
   # load(3000, 10, 14, 1, 128, 128, 128, 8),# game/models/game10_14_1_128_128_128_8_1500.tar
    load(6000, 10, 14, 1, 128, 128, 128, 8),
    load(3000, 10, 14, 3, 64, 64,64, 7),
    load(6000, 10, 14, 3, 64, 64,64, 7),
    load(1500, 10, 15, 1, 64, 64, 64, 7, 2), #game10_15_1_64_64_64_7_2_1500.tar
    load(1500, 10, 15, 2, 16, 16,16, 5, 2),
    load(6000, 10, 15, 1, 64, 64, 64, 7, 2),
    load(6000, 10, 15, 2, 16, 16,16, 5, 2),
]

Preparing dataset...
Samples in training set: 52
Samples in test set: 14

----------
Building model...
# Initializing model, trainer, and optimizer from game/models/game10_14_1_16_16_16_5_6000.tar
# loading trainer state from game/models/game10_14_1_16_16_16_5_6000.tar
SenderReceiverRnnReinforce(
  (sender): RnnSenderReinforce(
    (agent): LayerWrapper(
      (output): Linear(in_features=2, out_features=16, bias=True)
    )
    (hidden_to_output): Linear(in_features=16, out_features=16, bias=True)
    (embedding): Embedding(16, 5)
    (cells): ModuleList(
      (0): RNNCell(5, 16)
    )
  )
  (receiver): RnnReceiverDeterministic(
    (agent): LayerWrapper(
      (output): Linear(in_features=16, out_features=1, bias=True)
    )
    (encoder): RnnEncoder(
      (cell): RNN(5, 16, batch_first=True)
      (embedding): Embedding(16, 5)
    )
  )
  (mechanics): CommunicationRnnReinforce()
)
Number of parameters 1238

----------
Start of training... 2021-11-11 16:57:15.057005
{"loss": -0.128

{"loss": -0.17113696038722992, "acc": 0.7692307829856873, "sender_entropy": 0.6692924499511719, "receiver_entropy": 0.0, "length": 2.0, "mode": "train", "epoch": 6001}
End of training... 2021-11-11 16:57:17.099613
Duration: 0.28 seconds
Preparing dataset...
Samples in training set: 52
Samples in test set: 14

----------
Building model...
# Initializing model, trainer, and optimizer from game/models/game10_14_3_64_64_64_7_3000.tar
# loading trainer state from game/models/game10_14_3_64_64_64_7_3000.tar
SenderReceiverRnnReinforce(
  (sender): RnnSenderReinforce(
    (agent): LayerWrapper(
      (output): Linear(in_features=2, out_features=64, bias=True)
    )
    (hidden_to_output): Linear(in_features=64, out_features=64, bias=True)
    (embedding): Embedding(64, 7)
    (cells): ModuleList(
      (0): RNNCell(7, 64)
    )
  )
  (receiver): RnnReceiverDeterministic(
    (agent): LayerWrapper(
      (output): Linear(in_features=64, out_features=1, bias=True)
    )
    (encoder): RnnEncoder

# Test whole number range

In [102]:
run_test(games10, lambda x: test_all_set(x, 10))


--------
Running test for game 0
Testing 66 samples of numbers that sum up to 10
[0, 0] [12, 0] [0.6395790576934814] [0]
[0, 1] [0, 0] [0.8553138971328735] [1]
[0, 2] [2, 0] [2.6063244342803955] [2]
[0, 3] [2, 0] [2.6063244342803955] [3]
[0, 4] [15, 0] [4.512431621551514] [4]
[0, 5] [15, 0] [4.512431621551514] [5]
[0, 6] [13, 0] [5.992940425872803] [6]
[0, 7] [8, 0] [7.0237531661987305] [7]
[0, 8] [6, 0] [8.008564949035645] [8]
[0, 9] [7, 0] [9.51953125] [9]
[0, 10] [14, 0] [9.51669692993164] [10]
[1, 0] [0, 0] [0.8553138971328735] [1]
[1, 1] [2, 0] [2.6063244342803955] [2]
[1, 2] [2, 0] [2.6063244342803955] [3]
[1, 3] [15, 0] [4.512431621551514] [4]
[1, 4] [15, 0] [4.512431621551514] [5]
[1, 5] [13, 0] [5.992940425872803] [6]
[1, 6] [8, 0] [7.0237531661987305] [7]
[1, 7] [5, 0] [8.012918472290039] [8]
[1, 8] [11, 0] [9.506988525390625] [9]
[1, 9] [10, 0] [9.517173767089844] [10]
[2, 0] [2, 0] [2.6063244342803955] [2]
[2, 1] [2, 0] [2.6063244342803955] [3]
[2, 2] [15, 0] [4.5124316215

# Test validation only

In [47]:
run_test(games10, lambda x: test_validation_only(x))


--------
Running test for game 0
[5.0, 3.0] [5, 0] [8.012918472290039] [8.0]
[5.0, 2.0] [8, 0] [7.0237531661987305] [7.0]
[0.0, 10.0] [4, 0] [9.518916130065918] [10.0]
[7.0, 0.0] [8, 0] [7.0237531661987305] [7.0]
[5.0, 0.0] [15, 0] [4.512431621551514] [5.0]
[4.0, 0.0] [15, 0] [4.512431621551514] [4.0]
[0.0, 5.0] [15, 0] [4.512431621551514] [5.0]
[7.0, 3.0] [3, 0] [9.518096923828125] [10.0]
[1.0, 2.0] [2, 0] [2.6063244342803955] [3.0]
[1.0, 8.0] [7, 0] [9.51953125] [9.0]
[2.0, 8.0] [14, 0] [9.51669692993164] [10.0]
[2.0, 0.0] [2, 0] [2.6063244342803955] [2.0]
[4.0, 3.0] [8, 0] [7.023753643035889] [7.0]
[5.0, 1.0] [13, 0] [5.992940425872803] [6.0]
Unique outputs: 10: {2.6063244342803955, 4.512431621551514, 5.992940425872803, 7.0237531661987305, 8.012918472290039, 9.518916130065918, 9.518096923828125, 9.51953125, 9.51669692993164, 7.023753643035889}
Accuracy: 0.7857142686843872

--------
Running test for game 1
[5.0, 3.0] [4, 0] [8.426212310791016] [8.0]
[5.0, 2.0] [31, 0] [5.44823217391

[5.0, 3.0] [11, 14, 0] [7.977380752563477] [8.0]
[5.0, 2.0] [15, 7, 0] [7.011857032775879] [7.0]
[0.0, 10.0] [14, 14, 0] [9.87174129486084] [10.0]
[7.0, 0.0] [9, 2, 0] [6.85048770904541] [7.0]
[5.0, 0.0] [12, 3, 0] [4.981294631958008] [5.0]
[4.0, 0.0] [7, 9, 0] [3.9732015132904053] [4.0]
[0.0, 5.0] [11, 3, 0] [4.975295066833496] [5.0]
[7.0, 3.0] [13, 1, 0] [9.93853759765625] [10.0]
[1.0, 2.0] [3, 15, 0] [2.931697130203247] [3.0]
[1.0, 8.0] [1, 0, 0] [8.69810962677002] [9.0]
[2.0, 8.0] [15, 1, 0] [9.940787315368652] [10.0]
[2.0, 0.0] [4, 3, 0] [1.9693503379821777] [2.0]
[4.0, 3.0] [15, 4, 0] [7.04496955871582] [7.0]
[5.0, 1.0] [12, 4, 0] [5.961302757263184] [6.0]
Unique outputs: 14: {1.9693503379821777, 2.931697130203247, 3.9732015132904053, 4.981294631958008, 4.975295066833496, 6.85048770904541, 7.011857032775879, 7.977380752563477, 9.87174129486084, 9.93853759765625, 8.69810962677002, 9.940787315368652, 7.04496955871582, 5.961302757263184}
Accuracy: 1.0

--------
All games:
Game 0,  N

# Test above number range

In [48]:
start_numbers = [11, 13, 21, 101]
end_numbers = [12, 20, 100, 100000]
n_samples = [10, 100, 100, 1000]
run_test(games10, lambda x: test_various_ranges(x, start_numbers, end_numbers, n_samples))


--------
Running test for game 0
Testing 10 samples of numbers that sum up to [11 - 12]
[4, 7] [9, 0] [9.49213981628418] [11]
[5, 6] [4, 0] [9.518916130065918] [11]
[2, 10] [11, 0] [9.506988525390625] [12]
[11, 1] [10, 0] [9.517173767089844] [12]
[1, 10] [7, 0] [9.51953125] [11]
[6, 5] [10, 0] [9.517173767089844] [11]
[8, 4] [10, 0] [9.517173767089844] [12]
[10, 1] [11, 0] [9.506988525390625] [11]
[7, 4] [9, 0] [9.49213981628418] [11]
[0, 11] [10, 0] [9.517173767089844] [11]
Unique outputs: 5: {9.49213981628418, 9.517173767089844, 9.51953125, 9.518916130065918, 9.506988525390625}
Accuracy: 0.0
Testing 100 samples of numbers that sum up to [13 - 20]
[12, 2] [4, 0] [9.518916130065918] [14]
[14, 0] [9, 0] [9.49213981628418] [14]
[0, 20] [7, 0] [9.51953125] [20]
[16, 3] [11, 0] [9.506988525390625] [19]
[2, 18] [3, 0] [9.518096923828125] [20]
[12, 7] [14, 0] [9.51669692993164] [19]
[12, 8] [14, 0] [9.51669692993164] [20]
[2, 13] [7, 0] [9.51953125] [15]
[2, 11] [9, 0] [9.49213981628418] [1

[42750, 24644] [10, 0] [9.517173767089844] [67394]
[12103, 20682] [11, 0] [9.506988525390625] [32785]
[63799, 34742] [11, 0] [9.506988525390625] [98541]
[14148, 37995] [9, 0] [9.49213981628418] [52143]
[5915, 1387] [10, 0] [9.517173767089844] [7302]
[3184, 55811] [9, 0] [9.49213981628418] [58995]
[12707, 77404] [7, 0] [9.51953125] [90111]
[38560, 59144] [11, 0] [9.506988525390625] [97704]
[43981, 24234] [9, 0] [9.49213981628418] [68215]
[12324, 8553] [9, 0] [9.49213981628418] [20877]
[10427, 26060] [11, 0] [9.506988525390625] [36487]
[16429, 3305] [14, 0] [9.51669692993164] [19734]
[30419, 64576] [3, 0] [9.518096923828125] [94995]
[5990, 29017] [11, 0] [9.506988525390625] [35007]
[14323, 7532] [3, 0] [9.518096923828125] [21855]
[50993, 12541] [14, 0] [9.51669692993164] [63534]
[39550, 409] [4, 0] [9.518916130065918] [39959]
[90901, 3853] [14, 0] [9.51669692993164] [94754]
[14226, 41903] [14, 0] [9.51669692993164] [56129]
[30356, 39492] [4, 0] [9.518916130065918] [69848]
[171, 57051] [1

[0, 17736] [9, 0] [9.49213981628418] [17736]
[15788, 16675] [7, 0] [9.51953125] [32463]
[26466, 68521] [10, 0] [9.517173767089844] [94987]
[35565, 27908] [11, 0] [9.506988525390625] [63473]
[552, 50281] [4, 0] [9.518916130065918] [50833]
[22301, 20315] [9, 0] [9.49213981628418] [42616]
[86648, 5089] [10, 0] [9.517173767089844] [91737]
[20276, 10920] [14, 0] [9.51669692993164] [31196]
[15914, 24194] [7, 0] [9.51953125] [40108]
[10164, 2441] [10, 0] [9.517173767089844] [12605]
[1215, 706] [7, 0] [9.51953125] [1921]
[7761, 11272] [10, 0] [9.517173767089844] [19033]
[6391, 1907] [11, 0] [9.506988525390625] [8298]
[72697, 20818] [11, 0] [9.506988525390625] [93515]
[34585, 2860] [7, 0] [9.51953125] [37445]
[28130, 4595] [14, 0] [9.51669692993164] [32725]
[35316, 21268] [9, 0] [9.49213981628418] [56584]
[17652, 5433] [4, 0] [9.518916130065918] [23085]
[63311, 25879] [3, 0] [9.518096923828125] [89190]
[14009, 63893] [11, 0] [9.506988525390625] [77902]
[15123, 434] [7, 0] [9.51953125] [15557]
[

[606, 344] [20, 0] [10.242006301879883] [950]
[58600, 39573] [20, 0] [10.242006301879883] [98173]
[3735, 67827] [8, 0] [9.776081085205078] [71562]
[5221, 47661] [20, 0] [10.242006301879883] [52882]
[11008, 56459] [18, 0] [9.752037048339844] [67467]
[15340, 45570] [12, 0] [10.312610626220703] [60910]
[9379, 3466] [20, 0] [10.242006301879883] [12845]
[1060, 3135] [20, 0] [10.242006301879883] [4195]
[11218, 40148] [20, 0] [10.242006301879883] [51366]
[15476, 6130] [20, 0] [10.242006301879883] [21606]
[39825, 15462] [20, 0] [10.242006301879883] [55287]
[89, 46211] [20, 0] [10.242006301879883] [46300]
[12292, 35053] [20, 0] [10.242006301879883] [47345]
[47795, 37360] [20, 0] [10.242006301879883] [85155]
[90878, 4729] [12, 0] [10.312610626220703] [95607]
[27043, 26257] [18, 0] [9.752037048339844] [53300]
[10753, 53551] [12, 0] [10.312610626220703] [64304]
[49975, 3093] [12, 0] [10.312610626220703] [53068]
[58282, 7395] [20, 0] [10.242006301879883] [65677]
[30091, 6462] [12, 0] [10.3126106262

[4, 7] [13, 0] [9.965241432189941] [11]
[5, 6] [13, 0] [9.965241432189941] [11]
[2, 10] [26, 0] [9.28826904296875] [12]
[11, 1] [13, 0] [9.965241432189941] [12]
[1, 10] [17, 0] [9.291690826416016] [11]
[6, 5] [1, 0] [9.291207313537598] [11]
[8, 4] [2, 0] [9.284585952758789] [12]
[10, 1] [13, 0] [9.965241432189941] [11]
[7, 4] [13, 0] [9.965241432189941] [11]
[0, 11] [13, 0] [9.965241432189941] [11]
Unique outputs: 5: {9.965241432189941, 9.291207313537598, 9.284585952758789, 9.28826904296875, 9.291690826416016}
Accuracy: 0.0
Testing 100 samples of numbers that sum up to [13 - 20]
[12, 2] [13, 0] [9.965241432189941] [14]
[14, 0] [13, 0] [9.965241432189941] [14]
[0, 20] [13, 0] [9.965241432189941] [20]
[16, 3] [13, 0] [9.965241432189941] [19]
[2, 18] [13, 0] [9.965241432189941] [20]
[12, 7] [13, 0] [9.965241432189941] [19]
[12, 8] [13, 0] [9.965241432189941] [20]
[2, 13] [26, 0] [9.28826904296875] [15]
[2, 11] [13, 0] [9.965241432189941] [13]
[7, 9] [13, 0] [9.965241432189941] [16]
[2, 12

...

[37973, 51864] [45, 1, 0] [9.820154190063477] [89837]
[33410, 506] [40, 6, 0] [9.80163860321045] [33916]
[14334, 14175] [6, 10, 0] [9.802899360656738] [28509]
[15419, 10763] [43, 10, 0] [9.808226585388184] [26182]
[18634, 81031] [12, 10, 0] [9.810898780822754] [99665]
[7295, 58273] [3, 44, 0] [9.803193092346191] [65568]
[32645, 2599] [58, 45, 0] [9.80380630493164] [35244]
[53774, 30503] [12, 43, 0] [9.81921672821045] [84277]
[72163, 14971] [32, 5, 0] [9.802266120910645] [87134]
[33317, 1080] [43, 37, 0] [9.81407642364502] [34397]
[1378, 10344] [32, 10, 0] [9.801746368408203] [11722]
[34060, 49109] [54, 58, 0] [9.81387996673584] [83169]
[41271, 13826] [2, 49, 0] [9.80959415435791] [55097]
[6760, 3895] [12, 60, 0] [9.799357414245605] [10655]
[5925, 29303] [1, 3, 0] [9.805083274841309] [35228]
[13062, 7081] [14, 43, 0] [9.812599182128906] [20143]
[3763, 48636] [60, 58, 0] [9.806659698486328] [52399]
[19923, 34587] [44, 3, 0] [9.802149772644043] [54510]
[4403, 59270] [59, 60, 0] [9.7929849

[4, 7] [1, 0, 0] [9.129474639892578] [11]
[5, 6] [12, 1, 0] [9.170738220214844] [11]
[2, 10] [1, 5, 0] [9.738227844238281] [12]
[11, 1] [1, 14, 0] [9.742860794067383] [12]
[1, 10] [1, 5, 0] [9.738227844238281] [11]
[6, 5] [6, 15, 0] [9.653635025024414] [11]
[8, 4] [1, 13, 0] [9.742517471313477] [12]
[10, 1] [1, 6, 0] [9.743542671203613] [11]
[7, 4] [5, 1, 0] [8.958023071289062] [11]
[0, 11] [1, 12, 0] [9.733604431152344] [11]
Unique outputs: 9: {8.958023071289062, 9.129474639892578, 9.742860794067383, 9.653635025024414, 9.170738220214844, 9.738227844238281, 9.742517471313477, 9.743542671203613, 9.733604431152344}
Accuracy: 0.0
Testing 100 samples of numbers that sum up to [13 - 20]
[12, 2] [1, 6, 0] [9.743542671203613] [14]
[14, 0] [1, 15, 0] [9.737249374389648] [14]
[0, 20] [1, 14, 0] [9.742860794067383] [20]
[16, 3] [1, 6, 0] [9.743542671203613] [19]
[2, 18] [1, 14, 0] [9.742860794067383] [20]
[12, 7] [1, 14, 0] [9.742860794067383] [19]
[12, 8] [1, 8, 0] [9.694433212280273] [20]
[2, 

[4, 7] [16, 41, 0] [9.078776359558105] [11]
[5, 6] [18, 10, 0] [9.08644962310791] [11]
[2, 10] [21, 45, 0] [9.089682579040527] [12]
[11, 1] [54, 34, 0] [8.97962474822998] [12]
[1, 10] [1, 28, 0] [9.019864082336426] [11]
[6, 5] [6, 16, 0] [9.080162048339844] [11]
[8, 4] [37, 32, 0] [8.978364944458008] [12]
[10, 1] [18, 11, 0] [9.064790725708008] [11]
[7, 4] [18, 16, 0] [9.084503173828125] [11]
[0, 11] [14, 16, 0] [9.088994026184082] [11]
Unique outputs: 10: {8.97962474822998, 9.078776359558105, 9.019864082336426, 9.08644962310791, 9.089682579040527, 9.080162048339844, 8.978364944458008, 9.064790725708008, 9.084503173828125, 9.088994026184082}
Accuracy: 0.0
Testing 100 samples of numbers that sum up to [13 - 20]
[12, 2] [54, 25, 0] [8.995293617248535] [14]
[14, 0] [18, 44, 0] [9.064831733703613] [14]
[0, 20] [21, 18, 0] [9.086362838745117] [20]
[16, 3] [16, 60, 0] [9.087255477905273] [19]
[2, 18] [14, 39, 0] [9.080963134765625] [20]
[12, 7] [5, 39, 0] [9.091818809509277] [19]
[12, 8] [37

[5915, 1387] [5, 61, 0] [9.093318939208984] [7302]
[3184, 55811] [40, 39, 0] [9.023131370544434] [58995]
[12707, 77404] [26, 18, 0] [9.066964149475098] [90111]
[38560, 59144] [13, 14, 0] [9.08774471282959] [97704]
[43981, 24234] [12, 44, 0] [9.073140144348145] [68215]
[12324, 8553] [26, 18, 0] [9.066964149475098] [20877]
[10427, 26060] [18, 5, 0] [9.027117729187012] [36487]
[16429, 3305] [41, 18, 0] [9.072850227355957] [19734]
[30419, 64576] [37, 48, 0] [8.958242416381836] [94995]
[5990, 29017] [5, 44, 0] [9.091696739196777] [35007]
[14323, 7532] [45, 18, 0] [9.087408065795898] [21855]
[50993, 12541] [44, 56, 0] [9.066388130187988] [63534]
[39550, 409] [37, 12, 0] [9.013897895812988] [39959]
[90901, 3853] [14, 54, 0] [9.092011451721191] [94754]
[14226, 41903] [13, 37, 0] [9.090601921081543] [56129]
[30356, 39492] [13, 6, 0] [9.081226348876953] [69848]
[171, 57051] [56, 18, 0] [9.083257675170898] [57222]
[59889, 19877] [26, 37, 0] [9.080409049987793] [79766]
[78613, 4553] [41, 43, 0] [9

[15340, 45570] [1, 6, 0] [10.00866985321045] [60910]
[9379, 3466] [1, 13, 0] [9.996129989624023] [12845]
[1060, 3135] [1, 13, 0] [9.996129989624023] [4195]
[11218, 40148] [1, 14, 0] [10.008871078491211] [51366]
[15476, 6130] [6, 15, 0] [9.964634895324707] [21606]
[39825, 15462] [1, 12, 0] [9.972661972045898] [55287]
[89, 46211] [1, 8, 0] [9.969719886779785] [46300]
[12292, 35053] [1, 5, 0] [9.979081153869629] [47345]
[47795, 37360] [14, 15, 0] [9.956395149230957] [85155]
[90878, 4729] [1, 15, 0] [9.99439525604248] [95607]
[27043, 26257] [1, 1, 0] [10.012362480163574] [53300]
[10753, 53551] [1, 1, 0] [10.012362480163574] [64304]
[49975, 3093] [1, 8, 0] [9.969719886779785] [53068]
[58282, 7395] [1, 12, 0] [9.972661972045898] [65677]
[30091, 6462] [1, 1, 0] [10.012362480163574] [36553]
[30809, 51377] [14, 14, 0] [9.87174129486084] [82186]
[46083, 8430] [1, 15, 0] [9.99439525604248] [54513]
[28565, 932] [1, 13, 0] [9.996129989624023] [29497]
[22477, 20600] [1, 2, 0] [9.96731185913086] [430

# Test various numbers

In [49]:
run_test(games10, lambda x: test_some_other_numbers(x))


--------
Running test for game 0
[9.0, 0.2] [11, 0] [9.506988525390625] [9.2]
[0.0, 0.3] [12, 0] [0.6395790576934814] [0.3]
[6.0, 4.0] [4, 0] [9.518916130065918] [10.0]
[6.0, 4.0] [7, 0] [9.51953125] [10.0]
[9.0, 1.0] [11, 0] [9.506988525390625] [10.0]
[9.0, 1.0] [10, 0] [9.517173767089844] [10.0]
[9.0, 1.0] [3, 0] [9.518096923828125] [10.0]
[1.0, 1.0] [2, 0] [2.6063244342803955] [2.0]
[1.0, 1.0] [2, 0] [2.6063244342803955] [2.0]
[1.0, 1.0] [2, 0] [2.6063244342803955] [2.0]
[0.0, 1.0] [0, 0] [0.8553138971328735] [1.0]
[0.0, 0.0] [12, 0] [0.6395790576934814] [0.0]
[-1.0, 4.0] [2, 0] [2.6063244342803955] [3.0]
[5.0, -2.0] [2, 0] [2.6063244342803955] [3.0]
[-1.0, 0.0] [0, 0] [0.8553138971328735] [-1.0]
[-2.0, -2.0] [0, 0] [0.8553138971328735] [-4.0]
[-9.0, -1.0] [12, 0] [0.6395790576934814] [-10.0]
[8.0, -3.0] [15, 0] [4.512431621551514] [5.0]
[-10.0, -10.0] [0, 0] [0.8553138971328735] [-20.0]
Unique outputs: 9: {0.6395790576934814, 0.8553138971328735, 2.6063244342803955, 4.5124316215515

[-9.0, -1.0] [3, 3, 0] [0.3242495656013489] [-10.0]
[8.0, -3.0] [8, 3, 0] [5.204380035400391] [5.0]
[-10.0, -10.0] [3, 3, 0] [0.3242494463920593] [-20.0]
Unique outputs: 14: {0.3242495656013489, 1.3564751148223877, 2.621310234069824, 2.4026925563812256, 2.698326587677002, 2.905339479446411, 5.204380035400391, 0.3242494463920593, 8.534836769104004, 9.387617111206055, 9.737249374389648, 9.653635025024414, 9.542710304260254, 9.400053024291992}
Accuracy: 0.5263158082962036

--------
Running test for game 11
[9.0, 0.2] [18, 34, 0] [9.088879585266113] [9.2]
[0.0, 0.3] [47, 24, 0] [0.04041561484336853] [0.3]
[6.0, 4.0] [19, 13, 0] [9.069344520568848] [10.0]
[6.0, 4.0] [18, 16, 0] [9.084503173828125] [10.0]
[9.0, 1.0] [44, 13, 0] [9.053078651428223] [10.0]
[9.0, 1.0] [6, 39, 0] [9.054640769958496] [10.0]
[9.0, 1.0] [16, 44, 0] [9.083727836608887] [10.0]
[1.0, 1.0] [57, 9, 0] [1.996918797492981] [2.0]
[1.0, 1.0] [24, 24, 0] [2.002577543258667] [2.0]
[1.0, 1.0] [55, 47, 0] [2.648716688156128] [2

# Test synonymy

In [103]:
number_range = 10
repeat_times = 100
run_test(games10, lambda x: test_synonymy(x, 10, 100))


--------
Running test for game 0
[0, 0] [0, 0] [0.8553138971328735] [0]
[0, 0] [12, 0] [0.6395790576934814] [0]
[0, 0] [0, 0] [0.8553138971328735] [0]
[0, 0] [0, 0] [0.8553138971328735] [0]
[0, 0] [0, 0] [0.8553138971328735] [0]
[0, 0] [0, 0] [0.8553138971328735] [0]
[0, 0] [0, 0] [0.8553138971328735] [0]
[0, 0] [12, 0] [0.6395790576934814] [0]
[0, 0] [0, 0] [0.8553138971328735] [0]
[0, 0] [12, 0] [0.6395790576934814] [0]
[0, 0] [0, 0] [0.8553138971328735] [0]
[0, 0] [0, 0] [0.8553138971328735] [0]
[0, 0] [0, 0] [0.8553138971328735] [0]
[0, 0] [12, 0] [0.6395790576934814] [0]
[0, 0] [12, 0] [0.6395790576934814] [0]
[0, 0] [0, 0] [0.8553138971328735] [0]
[0, 0] [0, 0] [0.8553138971328735] [0]
[0, 0] [12, 0] [0.6395790576934814] [0]
[0, 0] [0, 0] [0.8553138971328735] [0]
[0, 0] [0, 0] [0.8553138971328735] [0]
[0, 0] [0, 0] [0.8553138971328735] [0]
[0, 0] [12, 0] [0.6395790576934814] [0]
[0, 0] [0, 0] [0.8553138971328735] [0]
[0, 0] [0, 0] [0.8553138971328735] [0]
[0, 0] [0, 0] [0.855313

[1, 1] [2, 0] [2.6063244342803955] [2]
[1, 1] [2, 0] [2.6063244342803955] [2]
[1, 1] [2, 0] [2.6063244342803955] [2]
[1, 1] [2, 0] [2.6063244342803955] [2]
[1, 1] [2, 0] [2.6063244342803955] [2]
[1, 1] [2, 0] [2.6063244342803955] [2]
[1, 1] [2, 0] [2.6063244342803955] [2]
[1, 1] [2, 0] [2.6063244342803955] [2]
[1, 1] [2, 0] [2.6063244342803955] [2]
[1, 1] [2, 0] [2.6063244342803955] [2]
[1, 1] [2, 0] [2.6063244342803955] [2]
[1, 1] [2, 0] [2.6063244342803955] [2]
[1, 1] [2, 0] [2.6063244342803955] [2]
[1, 1] [2, 0] [2.6063244342803955] [2]
[1, 1] [2, 0] [2.6063244342803955] [2]
[1, 1] [2, 0] [2.6063244342803955] [2]
[1, 1] [2, 0] [2.6063244342803955] [2]
[1, 1] [2, 0] [2.6063244342803955] [2]
[1, 1] [2, 0] [2.6063244342803955] [2]
[1, 1] [2, 0] [2.6063244342803955] [2]
[1, 1] [2, 0] [2.6063244342803955] [2]
[1, 1] [2, 0] [2.6063244342803955] [2]
[1, 1] [12, 0] [0.6395790576934814] [2]
[1, 1] [2, 0] [2.6063244342803955] [2]
[1, 1] [2, 0] [2.6063244342803955] [2]
[1, 1] [2, 0] [2.6063244

[1, 8] [7, 0] [9.51953125] [9]
[1, 8] [10, 0] [9.517173767089844] [9]
[1, 8] [7, 0] [9.51953125] [9]
[1, 8] [11, 0] [9.506988525390625] [9]
[1, 8] [9, 0] [9.49213981628418] [9]
[1, 8] [7, 0] [9.51953125] [9]
[1, 8] [14, 0] [9.51669692993164] [9]
[1, 8] [10, 0] [9.517173767089844] [9]
[1, 8] [3, 0] [9.518096923828125] [9]
[1, 8] [11, 0] [9.506988525390625] [9]
[1, 8] [14, 0] [9.51669692993164] [9]
[1, 8] [11, 0] [9.506988525390625] [9]
[1, 8] [7, 0] [9.51953125] [9]
[1, 8] [11, 0] [9.506988525390625] [9]
[1, 8] [9, 0] [9.49213981628418] [9]
[1, 8] [3, 0] [9.518096923828125] [9]
[1, 8] [14, 0] [9.51669692993164] [9]
[1, 8] [11, 0] [9.506988525390625] [9]
[1, 8] [9, 0] [9.49213981628418] [9]
[1, 8] [7, 0] [9.51953125] [9]
[1, 8] [10, 0] [9.517173767089844] [9]
[1, 8] [10, 0] [9.517173767089844] [9]
[1, 8] [3, 0] [9.518096923828125] [9]
[1, 8] [4, 0] [9.518916130065918] [9]
[1, 8] [10, 0] [9.517173767089844] [9]
[1, 8] [7, 0] [9.51953125] [9]
[1, 8] [10, 0] [9.517173767089844] [9]
[1, 8] [

[2, 6] [1, 0] [8.01823902130127] [8]
[2, 6] [5, 0] [8.012918472290039] [8]
[2, 6] [5, 0] [8.012918472290039] [8]
[2, 6] [1, 0] [8.01823902130127] [8]
[2, 6] [5, 0] [8.012918472290039] [8]
[2, 6] [5, 0] [8.012918472290039] [8]
[2, 6] [1, 0] [8.01823902130127] [8]
[2, 6] [5, 0] [8.012918472290039] [8]
[2, 6] [5, 0] [8.012918472290039] [8]
[2, 6] [1, 0] [8.01823902130127] [8]
[2, 6] [1, 0] [8.01823902130127] [8]
[2, 6] [5, 0] [8.012918472290039] [8]
[2, 6] [5, 0] [8.012918472290039] [8]
[2, 6] [5, 0] [8.012918472290039] [8]
[2, 6] [1, 0] [8.01823902130127] [8]
[2, 6] [6, 0] [8.008564949035645] [8]
[2, 6] [6, 0] [8.008564949035645] [8]
[2, 6] [6, 0] [8.008564949035645] [8]
[2, 6] [6, 0] [8.008564949035645] [8]
[2, 6] [5, 0] [8.012918472290039] [8]
[2, 6] [1, 0] [8.01823902130127] [8]
[2, 6] [5, 0] [8.012918472290039] [8]
[2, 6] [6, 0] [8.008564949035645] [8]
[2, 6] [6, 0] [8.008564949035645] [8]
[2, 6] [5, 0] [8.012918472290039] [8]
[2, 6] [5, 0] [8.012918472290039] [8]
[2, 6] [5, 0] [8.01

[3, 7] [10, 0] [9.517173767089844] [10]
[3, 7] [3, 0] [9.518096923828125] [10]
[3, 7] [10, 0] [9.517173767089844] [10]
[3, 7] [7, 0] [9.51953125] [10]
[3, 7] [14, 0] [9.51669692993164] [10]
[3, 7] [14, 0] [9.51669692993164] [10]
[3, 7] [11, 0] [9.506988525390625] [10]
[3, 7] [11, 0] [9.506988525390625] [10]
[3, 7] [10, 0] [9.517173767089844] [10]
[3, 7] [10, 0] [9.517173767089844] [10]
[3, 7] [7, 0] [9.51953125] [10]
[3, 7] [14, 0] [9.51669692993164] [10]
[3, 7] [11, 0] [9.506988525390625] [10]
[3, 7] [4, 0] [9.518916130065918] [10]
[3, 7] [7, 0] [9.51953125] [10]
[3, 7] [3, 0] [9.518096923828125] [10]
[3, 7] [3, 0] [9.518096923828125] [10]
[3, 7] [14, 0] [9.51669692993164] [10]
[3, 7] [3, 0] [9.518096923828125] [10]
[3, 7] [10, 0] [9.517173767089844] [10]
[3, 7] [9, 0] [9.49213981628418] [10]
[3, 7] [7, 0] [9.51953125] [10]
[3, 7] [14, 0] [9.51669692993164] [10]
[3, 7] [9, 0] [9.49213981628418] [10]
[3, 7] [7, 0] [9.51953125] [10]
[3, 7] [10, 0] [9.517173767089844] [10]
[3, 7] [7, 0] 

...

[3, 3] [11, 7, 0] [5.965977668762207] [6]
[3, 3] [12, 0, 0] [5.9873456954956055] [6]
[3, 3] [11, 10, 0] [5.95343017578125] [6]
[3, 3] [9, 10, 0] [5.948479652404785] [6]
[3, 3] [8, 7, 0] [5.964536666870117] [6]
[3, 3] [12, 4, 0] [5.961302757263184] [6]
[3, 3] [5, 4, 0] [5.970867156982422] [6]
[3, 3] [15, 3, 0] [5.975342750549316] [6]
[3, 3] [12, 7, 0] [5.958651542663574] [6]
[3, 3] [13, 3, 0] [5.951824188232422] [6]
[3, 3] [5, 10, 0] [5.957562446594238] [6]
[3, 3] [11, 4, 0] [5.9694318771362305] [6]
[3, 3] [15, 3, 0] [5.975342750549316] [6]
[3, 3] [13, 3, 0] [5.951824188232422] [6]
[3, 3] [12, 10, 0] [5.95604133605957] [6]
[3, 3] [11, 7, 0] [5.965977668762207] [6]
[3, 3] [8, 4, 0] [5.967700958251953] [6]
[3, 3] [13, 3, 0] [5.951824188232422] [6]
[3, 3] [2, 8, 0] [5.9102277755737305] [6]
[3, 3] [12, 7, 0] [5.958651542663574] [6]
[3, 3] [8, 10, 0] [5.970401763916016] [6]
[3, 3] [9, 7, 0] [5.952540397644043] [6]
[3, 3] [9, 10, 0] [5.948479652404785] [6]
[3, 3] [2, 12, 0] [5.891974449157715

[4, 5] [8, 1, 0] [8.953465461730957] [9]
[4, 5] [5, 1, 0] [8.947943687438965] [9]
[4, 5] [11, 1, 0] [8.945673942565918] [9]
[4, 5] [11, 1, 0] [8.945673942565918] [9]
[4, 5] [1, 7, 0] [8.957209587097168] [9]
[4, 5] [13, 15, 0] [8.970440864562988] [9]
[4, 5] [13, 13, 0] [8.94454288482666] [9]
[4, 5] [5, 1, 0] [8.947943687438965] [9]
[4, 5] [6, 8, 0] [8.994308471679688] [9]
[4, 5] [8, 1, 0] [8.953465461730957] [9]
[4, 5] [6, 11, 0] [9.003552436828613] [9]
[4, 5] [14, 12, 0] [8.984761238098145] [9]
[4, 5] [9, 1, 0] [8.94225025177002] [9]
[4, 5] [12, 1, 0] [8.946087837219238] [9]
[4, 5] [11, 1, 0] [8.945673942565918] [9]
[4, 5] [8, 1, 0] [8.953465461730957] [9]
[4, 5] [15, 13, 0] [9.023748397827148] [9]
[4, 5] [15, 6, 0] [8.939167976379395] [9]
[4, 5] [14, 2, 0] [8.926835060119629] [9]
[4, 5] [13, 14, 0] [8.888781547546387] [9]
[4, 5] [15, 15, 0] [9.051973342895508] [9]
[4, 5] [11, 1, 0] [8.945673942565918] [9]
[4, 5] [12, 1, 0] [8.946087837219238] [9]
[4, 5] [1, 0, 0] [8.69810962677002] [9

[6, 3] [11, 1, 0] [8.945673942565918] [9]
[6, 3] [14, 5, 0] [8.99721908569336] [9]
[6, 3] [1, 4, 0] [8.96264362335205] [9]
[6, 3] [8, 1, 0] [8.953465461730957] [9]
[6, 3] [6, 5, 0] [8.999990463256836] [9]
[6, 3] [1, 10, 0] [8.974688529968262] [9]
[6, 3] [15, 6, 0] [8.939167976379395] [9]
[6, 3] [15, 14, 0] [8.92824935913086] [9]
[6, 3] [13, 14, 0] [8.888781547546387] [9]
[6, 3] [14, 12, 0] [8.984761238098145] [9]
[6, 3] [6, 11, 0] [9.003552436828613] [9]
[6, 3] [15, 14, 0] [8.92824935913086] [9]
[6, 3] [14, 12, 0] [8.984761238098145] [9]
[6, 3] [1, 4, 0] [8.96264362335205] [9]
[6, 3] [14, 9, 0] [8.980374336242676] [9]
[6, 3] [15, 13, 0] [9.023748397827148] [9]
[6, 3] [14, 8, 0] [8.989920616149902] [9]
[6, 3] [14, 12, 0] [8.984761238098145] [9]
[6, 3] [13, 14, 0] [8.888781547546387] [9]
[6, 3] [1, 10, 0] [8.974688529968262] [9]
[6, 3] [6, 5, 0] [8.999990463256836] [9]
[6, 3] [13, 14, 0] [8.888781547546387] [9]
[6, 3] [14, 8, 0] [8.989920616149902] [9]
[6, 3] [15, 14, 0] [8.9282493591308

[7, 3] [1, 15, 0] [9.99439525604248] [10]
[7, 3] [14, 14, 0] [9.87174129486084] [10]
[7, 3] [15, 1, 0] [9.940787315368652] [10]
[7, 3] [1, 13, 0] [9.996129989624023] [10]
[7, 3] [15, 1, 0] [9.940787315368652] [10]
[7, 3] [15, 1, 0] [9.940787315368652] [10]
[7, 3] [15, 1, 0] [9.940787315368652] [10]
[7, 3] [13, 1, 0] [9.93853759765625] [10]
[7, 3] [15, 1, 0] [9.940787315368652] [10]
[7, 3] [6, 1, 0] [9.941119194030762] [10]
[7, 3] [14, 13, 0] [9.915885925292969] [10]
[7, 3] [13, 1, 0] [9.93853759765625] [10]
[7, 3] [14, 6, 0] [9.897052764892578] [10]
[7, 3] [1, 14, 0] [10.008871078491211] [10]
[7, 3] [14, 1, 0] [9.940850257873535] [10]
[7, 3] [15, 1, 0] [9.940787315368652] [10]
[7, 3] [13, 1, 0] [9.93853759765625] [10]
[7, 3] [6, 15, 0] [9.964634895324707] [10]
[7, 3] [14, 1, 0] [9.940850257873535] [10]
[7, 3] [13, 6, 0] [8.90208911895752] [10]
[7, 3] [14, 6, 0] [9.897052764892578] [10]
[7, 3] [15, 1, 0] [9.940787315368652] [10]
[7, 3] [13, 1, 0] [9.93853759765625] [10]
[7, 3] [13, 1, 0

[8, 2] [6, 14, 0] [9.888434410095215] [10]
[8, 2] [6, 15, 0] [9.964634895324707] [10]
[8, 2] [6, 15, 0] [9.964634895324707] [10]
[8, 2] [13, 1, 0] [9.93853759765625] [10]
[8, 2] [6, 6, 0] [9.910877227783203] [10]
[8, 2] [14, 6, 0] [9.897052764892578] [10]
[8, 2] [13, 1, 0] [9.93853759765625] [10]
[8, 2] [14, 6, 0] [9.897052764892578] [10]
[8, 2] [15, 1, 0] [9.940787315368652] [10]
[8, 2] [1, 15, 0] [9.99439525604248] [10]
[8, 2] [1, 12, 0] [9.972661972045898] [10]
[8, 2] [14, 6, 0] [9.897052764892578] [10]
[8, 2] [1, 6, 0] [10.00866985321045] [10]
[8, 2] [6, 13, 0] [9.930745124816895] [10]
[8, 2] [1, 5, 0] [9.979081153869629] [10]
[8, 2] [14, 13, 0] [9.915885925292969] [10]
[8, 2] [6, 6, 0] [9.910877227783203] [10]
[8, 2] [13, 1, 0] [9.93853759765625] [10]
[8, 2] [1, 1, 0] [10.012362480163574] [10]
[8, 2] [1, 15, 0] [9.99439525604248] [10]
[8, 2] [13, 1, 0] [9.93853759765625] [10]
[8, 2] [15, 1, 0] [9.940787315368652] [10]
[8, 2] [1, 13, 0] [9.996129989624023] [10]
[8, 2] [1, 2, 0] [9.

---

In [32]:
def load_run(epochs, last_save, model_size, model_number, run_number, vocab, sender, receiver, embedding, length=1):
    epochs = epochs
    save_name = "game/models/game{}_{}_{}_{}_{}_{}_{}".format(model_size, model_number, run_number, vocab, sender, receiver, embedding)
    if(length > 1):
        save_name = "{}_{}".format(save_name, length)
    

    params = [
        '--batch_size=1',
        '--n_epochs={}'.format(epochs),
        '--vocab_size={}'.format(vocab),
        '--sender_hidden={}'.format(sender),
        '--receiver_hidden={}'.format(receiver),
        '--lr=0.001',
        '--max_len={}'.format(length),
        '--sender_entropy=0.5',
        '--sender_embedding={}'.format(embedding),
        '--receiver_embedding={}'.format(embedding),
        '--validation_freq=10',
        '--train_data=game/data/train10.txt',
        '--validation_data=game/data/validation10.txt',
        '--load_from_checkpoint={}_{}.tar'.format(save_name, last_save)
    ]
    game = Game(params)
    game.play()
    game.save_checkpoint(epochs, save_name)
    return game

In [ ]:

#Checkpoint saved at game/models/game10_14_1_128_128_128_8_1500.tar
# load_run(3000, 1500, 10, 14, 1, 128, 128, 128, 8)